# 📍 Visualización de Plusvalía Inmobiliaria — Valdivia

Este notebook carga los resultados procesados desde `data/processed/plusvalia_valdivia.geojson` y genera un mapa interactivo con Folium.

In [4]:
import geopandas as gpd
import folium
from folium.plugins import MarkerCluster

# Cargar datos
manzanas = gpd.read_file("../data/processed/plusvalia_valdivia.geojson")
servicios = gpd.read_file("../data/processed/servicios.geojson")

# Crear mapa base centrado en Valdivia
m = folium.Map(location=[-39.8, -73.25], zoom_start=13)

# Capa de choropleth con plusvalía
folium.Choropleth(
    geo_data=manzanas,
    data=manzanas,
    columns=['COD_MANZAN', 'score'],
    key_on='feature.properties.COD_MANZAN',
    fill_color='YlOrRd',
    fill_opacity=0.7,
    line_opacity=0.2,
    legend_name='Potencial de Plusvalía'
).add_to(m)

# Capa de servicios públicos (cluster de marcadores)
marker_cluster = MarkerCluster().add_to(m)
for _, row in servicios.iterrows():
    punto = row.geometry.centroid  # Si son puntos no hace falta centroid, pero por seguridad
    folium.Marker(
        location=[punto.y, punto.x],
        popup=row['name'],
        icon=folium.Icon(color='blue', icon='info-sign')
    ).add_to(marker_cluster)

# Leyenda personalizada
legend_html = """
 <div style="position: fixed; 
             bottom: 40px; left: 40px; width: 250px; height: 160px; 
             background-color: white; z-index:9999; font-size:14px;
             border:2px solid grey; border-radius:10px; padding: 10px;">
 <b>🔎 Leyenda</b><br>
 🟥 Alta plusvalía<br>
 🟧 Media-alta<br>
 🟨 Media<br>
 🟩 Baja<br>
 📍 Servicios (Azul)<br>
 </div>
"""
m.get_root().html.add_child(folium.Element(legend_html))

# Mostrar mapa
m